In [1]:
import pandas as pd
import os

AWS_PATH = '../../records/blocks/aws/'
FORKED_PATH = '../crawler/forked_json/'

In [2]:
forked_df = None

for filename in os.listdir(FORKED_PATH):
    if filename.endswith(".txt"):
        print('loading ', FORKED_PATH + filename)
        new_forked = pd.read_json(FORKED_PATH + filename, lines=True)
        forked_df = pd.concat([forked_df, new_forked], ignore_index=True)
    break
print(forked_df.shape)
forked_df.head()

loading  ../crawler/forked_json/2017-05-24.txt
(50, 18)


difficulty                                          extraData  \
0  0x19e2483cc57dd  EtherMine.RU/DGM FTW (Hex:0x45746865724d696e65...   
1  0x19da0ec4bd45e  01050b/Parity/1.15.1/li (Hex:0xd58301050b86506...   
2  0x1a08f16bc5653  ethpool - ASIA1 (Hex:0x657468706f6f6c202d20415...   
3  0x19d2459bba652  Alpereum EUROPE (Hex:0x416c70657265756d2045555...   
4  0x1a015b46bf35c  01040c/Parity/1.15.1/li (Hex:0xd58301040c86506...   

   gasLimit   gasUsed                                               hash  \
0  0x41ad52  0x41964a  0xa6a9619bce6c502ff4ebec42e84c63f5df6308b65386...   
1  0x419aad    0x5208  0x8bea49e0d3a8bb0cd542d01fccfa54e6d202fc00b5a1...   
2  0x41c44d  0x1cf9a0  0xf39fd2db843a3a6c938c66b57803c517106e285c63bc...   
3  0x421eec  0x3feba4  0x7ede2d957885010f38c062453bcb60931a7a9549e772...   
4  0x41acbe  0x386a15  0x9babb5eb0b51c8104d74cc2c8b52e31fe322ca57478b...   

   mineTime                                       miner     minerName nonce  \
0        48  0x215c86bc952b0d98c4b2313a0a9ae56fa33c7f5d  Ethermine.ru    0x   
1         3  0xa42af2c70d316684e57aefcc6e393fecb1c7e84e   Coinotron 2    0x   
2        13  0x4bb96091ee9d802ed039c4d1a5f6216f90f81b01     Ethpool 2    0x   
3        39  0x6c7f03ddfdd8a37ca267c88630a4fee958591de0      alpereum    0x   
4        18  0xf3b9d2c81f2b24b0fa0acaaa865b7d9ced5fc2fb   BitClubPool    0x   

     number                                         parentHash reorgDepth  \
0  0x39684e  0x41075e262b99d531c90f86a36660696d68585eeb60c5...              
1  0x396837  0xf0bbe5fafdeb982dfccc7559ac24f206446600b6a4da...              
2  0x396735  0x6200a95ee559f3acc48fc00cc55f9f9c4e3a4d19dfb1...              
3  0x3966db  0x62e0b0a73d966ed10eefd833af79f3be02647fa5ff6d...              
4  0x396676  0xf7a0f111a595380f388de409fe24129a35cbc153b50d...              

     reward                                         sha3Uncles    size  \
0  5.105547  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x2bbf   
1  5.001050  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...   0x28f   
2  5.041857  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x20a9   
3  5.126846  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x3dec   
4  5.083431  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x1ebe   

    timestamp      totalDifficulty uncleReward  
0  0x59267ab7  0xfa035f22a597adc77           0  
1  0x5926796a  0xfa010b7cfe0ac3da8           0  
2  0x59266902  0xf9e6d88d91b1762f6           0  
3  0x592663db  0xf9ddbe2c6e91676ad           0  
4  0x59265ce8  0xf9d37c1bb17dcfc05           0

In [5]:
type(forked_df.timestamp[0])

str

# Prepare Dataset

Read raw block files and convert them to pandas dataframe.

In [100]:
all_broadcast = dict() #  dict[hash] = [block_info]

## Broadcast Blocks

In [101]:
def parse_one_broadcast(line):
    temp_list = []
    
#     print(line)
    b_hash = line.split('Block Hash=')[1].split(', parentHash')[0]
    if 'difficulty=' in line:
        difficulty = line.split('difficulty=')[1].split(', ')[0]
    else:
        difficulty = '-1'
    gasLimit = line.split('gasLimit=')[1].split(', ')[0]
    gasUsed = line.split('gasUsed=')[1].split(', gasLimit')[0]
    logsBloom = line.split('logsBloom=')[1].split(', number=')[0]
    miner = line.split('miner=')[1].split(', uncleNum=')[0]
    timestamp = line.split('timestamp=')[1]
    uncles = line.split('uncleNum=')[1].split(', txNum=')[0]

    temp_list.append(b_hash)
    temp_list.append(difficulty)
    temp_list.append(gasLimit)
    temp_list.append(gasUsed)
    temp_list.append(logsBloom)
    temp_list.append(miner)
    temp_list.append(timestamp)
    temp_list.append(uncles)
    
    return b_hash, temp_list

In [102]:
def load_broadcasts(folder_path):
#     for filename in os.listdir(folder_path):
    for filename in ['2019-07-09.txt', '2019-07-10.txt']:
#         if filename.endswith(".txt"):
#             print(filename)
#     with open(folder_path + '2019-07-09.txt', encoding='"ISO-8859-1"') as f:
        with open(folder_path + filename) as f:
            while True:
                line = f.readline()
                if not line:
                    break
                if 'Block Hash=' in line:
                    b_hash, b_info_list = parse_one_broadcast(line)
    #                 print(b_hash)
    #                 print(b_info_list)
                    all_broadcast[b_hash] = b_info_list

In [103]:
load_broadcasts(AWS_PATH)

In [105]:
broadcast_df = pd.DataFrame.from_dict(all_broadcast, orient='index', columns=['hash', 'difficulty', 'gasLimit', 'gasUsed', 'logsBloom', 'miner', 'timestamp', 'uncles' ])





In [106]:
broadcast_df.shape

(13895, 8)

In [107]:
len(all_broadcast)

13895

In [108]:
broadcast_df.head()

hash  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  0x869d968cbd5404f81d8fa750eb4672f4752db1979474...   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e07...   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  0x5997952fe4090ee366df6be1dc711424dd236f9c5909...   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9a...   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e...   

                                                          difficulty gasLimit  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  2119842492649275  8003760   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  2119843029520187  8002886   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  2119843566391099  8000029   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  2119844103262011  8000029   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  2117774479875833  8000000   

                                                    gasUsed  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  4738605   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  3784627   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  7963577   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  7988313   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  7930872   

                                                                                            logsBloom  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  0221218a04322008408904084268000981003008400000...   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  000050000000002a845c00002408901421c230c2011020...   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  1a2c3f72e442e81249c1040b06c4dd4010a8f00bd92140...   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  0b0018c00010a40a044323088201484cd88bb000868128...   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  2000318a0c4221020301042f42081077180822002a9008...   

                                                                                         miner  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  0x5A0b54D5dc17e0AadC383d2db43B0a0D3E029c4c   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  0x5A0b54D5dc17e0AadC383d2db43B0a0D3E029c4c   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  0x52bc44d5378309EE2abF1539BF71dE1b7d7bE3b5   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  0x52bc44d5378309EE2abF1539BF71dE1b7d7bE3b5   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  0xEA674fdDe714fd979de3EdF0F56AA9716B898ec8   

                                                                          timestamp  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  2019-07-08 23:59:50 +0800 CST\n   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  2019-07-08 23:59:59 +0800 CST\n   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  2019-07-09 00:00:08 +0800 CST\n   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  2019-07-09 00:00:21 +0800 CST\n   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  2019-07-09 00:00:54 +0800 CST\n   

                                                   uncles  
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...      0  
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...      0  
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...      0  
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...      0  
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...      0

## Canonical Blocks

In [109]:
CANONICAL_PATH = '../crawler/canonical_temp/'

In [110]:
canonical_df = None

for filename in os.listdir(CANONICAL_PATH):
    if filename.endswith(".txt"):
        print('loading ', filename)
        new_canonical = pd.read_json(CANONICAL_PATH + filename, lines=True)
        canonical_df = pd.concat([canonical_df, new_canonical], ignore_index=True)

print(canonical_df.shape)
canonical_df.head()

loading  8110000.txt
loading  8090000.txt
loading  8100000.txt
loading  8120000.txt
(28214, 20)


difficulty                                          extraData  \
0  0x7cc30b6f71e6f         0x505059452d65746865726d696e652d6575312d32   
1  0x7cb3730111c4c  0x5050594520737061726b706f6f6c2d6574682d636e2d...   
2  0x7cb3710111c4c         0x7070796520e4b883e5bda9e7a59ee4bb99e9b1bc   
3  0x7cd2a3a9fc43c           0x5050594520636f696e6f74726f6e2d65752d32   
4  0x7cd2a1a9fc43c         0x7070796520e4b883e5bda9e7a59ee4bb99e9b1bc   

   gasLimit   gasUsed                                               hash  \
0  0x7a1200  0x28e529  0x2e9951468126727a895d262f25c936c04f5a3a5146e0...   
1  0x7a2536  0x79c8bd  0x3c74cf01fe950a6752ead673f7018e09689d47d819a2...   
2  0x7a30a0  0x3303b5  0xe970940b6b6362145b453e65cf4c957ae64d8f11d181...   
3  0x7a121d  0x1b027b  0x3967be3827507a2aa36f17491140c6d9a1608a0fc6e7...   
4  0x7a30a0  0x23aab2  0x9e42a0bc15152bd5387e807c9022bbe8517225db16bf...   

                                           logsBloom  \
0  0x04002020002008480044220840100500811012000900...   
1  0x000432d210128040005a040802102cb3651810a681c1...   
2  0x0802a0a3000489a80300280205483210040004002010...   
3  0x0200400200100000002800000000000b020000008008...   
4  0x00200080084838038000240000204000002000035000...   

                                        miner  \
0  0xea674fdde714fd979de3edf0f56aa9716b898ec8   
1  0x5a0b54d5dc17e0aadc383d2db43b0a0d3e029c4c   
2  0x829bd824b016326a401d083b33d092293333a830   
3  0x6a7a43be33ba930fe58f34e07d0ad6ba7adb9b1f   
4  0x829bd824b016326a401d083b33d092293333a830   

                                             mixHash               nonce  \
0  0x3d176b4ad35259fb81e5df4ed3b8224a57a51edc264c...  0xb376950c0288a6f1   
1  0x97fcf5c68abb39977e62d97f6269500c633285f7b2c7...  0x6e30d758007f1ca9   
2  0x4228156276f268341257f2e217a8d0beb897e6231829...  0x6b270c0014d6d957   
3  0xb2fca85a45db1d3b3fae4a6ec879c79f933b89d2865d...  0xb0558f0405ac2f92   
4  0xe8eb80c812f051288595f8ff0db9e59fcf54c6fdafdd...  0x4663fbe0034833b7   

     number                                         parentHash  \
0  0x7be6bf  0x3c74cf01fe950a6752ead673f7018e09689d47d819a2...   
1  0x7be6be  0xe970940b6b6362145b453e65cf4c957ae64d8f11d181...   
2  0x7be6bd  0x3967be3827507a2aa36f17491140c6d9a1608a0fc6e7...   
3  0x7be6bc  0x9e42a0bc15152bd5387e807c9022bbe8517225db16bf...   
4  0x7be6bb  0x4a1ba0e8087a59062edc721eabe130570fe07a16976a...   

                                        receiptsRoot  \
0  0x47980ef96d48fabd88b2ff749bbc5ccc040d9f1e5251...   
1  0xdb13f54560d4dbcee0e992ceb06fa7755986de55b9f7...   
2  0x26ccd662ea6857251d6a6d2b3101a13b1866d1810477...   
3  0x454451fff2679f5dbde5cc40c91f3548dc6d78424b2a...   
4  0x63ddcd2e9bfb7d3be8b20b1d3b6484ce4b1ae4baa1c1...   

                                          sha3Uncles    size  \
0  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x24da   
1  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x48ba   
2  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x3b65   
3  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x218e   
4  0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a...  0x2768   

                                           stateRoot   timestamp  \
0  0x20c8d28b9efdb221493f01583c7c1a06148f8fcb77d9...  0x5d252226   
1  0x265041151c528da75f69840f7945427a40c6a8ed7586...  0x5d252225   
2  0x5233449148116a5ecbae8bd386fae210cc647f44e8dd...  0x5d252216   
3  0x1ab48a08718194e63ed1cf6f81e57fcbeb3ef4027506...  0x5d2521fb   
4  0x416c0c0f9875b2b1aff7425923fbc1efe26cf3aa9138...  0x5d2521f2   

         totalDifficulty                                       transactions  \
0  0x2516840bcbadd9641dc  [0x713237e3fb568036f25bb44e26936d8210805a7c3b5...   
1  0x2516838f08a269f236d  [0x5adacf50553d21628d8db4c454574a5ee9d0b67358f...   
2  0x25168312552f68e0721  [0x7c7a5566b7e5d88ce8a0de6ca275063cb72716eed94...   
3  0x25168295a1be67cead5  [0x5c6257d3117d94518d5bb2b3e862c0d72369b7698e3...   
4  0x25168218cf1abdd2699  [0xd0dbb3470281e5c71636d5c8e465ee7dcbc57a0cae0...   

                    

### Delete canonical from broadcast

In [127]:
broadcast_hashes = broadcast_df.hash

In [129]:
counter = 0
drop_list = []
non_canonical_list = []
for b_hash in broadcast_hashes:
    if b_hash in canonical_df.hash.values:
        counter += 1
#         broadcast_df.drop(b_hash)
        drop_list.append(b_hash)
    else:
        non_canonical_list.append(b_hash)
broadcast_df.drop(drop_list)

print(broadcast_df.shape)
print(counter)
print(len(non_canonical_list))
broadcast_df.head()

(13895, 8)
12924
971


hash  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  0x869d968cbd5404f81d8fa750eb4672f4752db1979474...   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e07...   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  0x5997952fe4090ee366df6be1dc711424dd236f9c5909...   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9a...   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e...   

                                                          difficulty gasLimit  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  2119842492649275  8003760   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  2119843029520187  8002886   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  2119843566391099  8000029   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  2119844103262011  8000029   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  2117774479875833  8000000   

                                                    gasUsed  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  4738605   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  3784627   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  7963577   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  7988313   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  7930872   

                                                                                            logsBloom  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  0221218a04322008408904084268000981003008400000...   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  000050000000002a845c00002408901421c230c2011020...   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  1a2c3f72e442e81249c1040b06c4dd4010a8f00bd92140...   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  0b0018c00010a40a044323088201484cd88bb000868128...   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  2000318a0c4221020301042f42081077180822002a9008...   

                                                                                         miner  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  0x5A0b54D5dc17e0AadC383d2db43B0a0D3E029c4c   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  0x5A0b54D5dc17e0AadC383d2db43B0a0D3E029c4c   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  0x52bc44d5378309EE2abF1539BF71dE1b7d7bE3b5   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  0x52bc44d5378309EE2abF1539BF71dE1b7d7bE3b5   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  0xEA674fdDe714fd979de3EdF0F56AA9716B898ec8   

                                                                          timestamp  \
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...  2019-07-08 23:59:50 +0800 CST\n   
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...  2019-07-08 23:59:59 +0800 CST\n   
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...  2019-07-09 00:00:08 +0800 CST\n   
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...  2019-07-09 00:00:21 +0800 CST\n   
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...  2019-07-09 00:00:54 +0800 CST\n   

                                                   uncles  
0x869d968cbd5404f81d8fa750eb4672f4752db1979474b...      0  
0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e075...      0  
0x5997952fe4090ee366df6be1dc711424dd236f9c59090...      0  
0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9ab...      0  
0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e7...      0

In [137]:
temp_index = pd.Series(list(range(len(broadcast_hashes))))
broadcast_df.set_index(temp_index)

hash        difficulty  \
0      0x869d968cbd5404f81d8fa750eb4672f4752db1979474...  2119842492649275   
1      0x86c7e5fd62d71430be8292ac909df6a1b3730aae7e07...  2119843029520187   
2      0x5997952fe4090ee366df6be1dc711424dd236f9c5909...  2119843566391099   
3      0x8a673122efccbf1b7693da1212e2b8a482c22c58bd9a...  2119844103262011   
4      0x3e0f3cbf2f186b45a41a5a9dea65ab156fef54e3c37e...  2117774479875833   
5      0xd9fd2045b21d44a888ee6615c5045777255d668734e5...                -1   
6      0x044c65b4d0ba42f1dfd1526dfe3923339dc5a8fe385a...                -1   
7      0x4f82f4e508eb0ad04a57af29bb6e7dd93376598b4a96...                -1   
8      0xdc41c48b19868e2ce2ac683809c8d1775f98b15b6073...                -1   
9      0x40e8666445cb693909846ad6fa312ffbc11bb64567f1...  2115702964471843   
10     0x68fa1a34d9bed424e59ad173ce3b40d783ca36ce54dc...  2113637385166513   
11     0xf2fb1ece1f1b70095571502980078f1aca053ae72080...                -1   
12     0xc629aa64b55ef57696b256f414a18dc3e7b618c749ad...                -1   
13     0x2d9db9e50ac5ab5686f0df6f01ce261e157148538623...                -1   
14     0xc481747630b8cd85a90bfef15bdf7a6aa2a8a5606c1b...                -1   
15     0xf91cba8fe5a25b38422539349b7b795272e2818c3aff...                -1   
16     0xd47ecbfb8dd3e82471f2ff98f353e6cc6d082815c40a...                -1   
17     0xa5097f7ee79213971b882ff9b748dc96065921fee69f...  2114666572061969   
18     0x278e41422cc719394af3a1fb960c25a2dbff556b14d4...  2115699660970020   
19     0x6597e52311b11f44b2499b9c6dca32168e179b9a6d11...  2114667141365849   
20     0x1568ad912a20499c0bb61b2d7e10e1a759aa389abbe8...  2114667678236761   
21     0x00ad17f704c63780420e6450bf6038b4338a0ebecc88...                -1   
22     0x13bfa5d81127eaec4c3966d8e5846baf86e64a215b2a...                -1   
23     0x90f3c4a8e1a6b746f1e9aaa76ebf1f4bc66a44466579...                -1   
24     0xcc4cd97826bcf2addd3d103b47e2a5df5a13485d8c92...  2111572638159369   
25     0x2b5e65816fb6b39834044a1631c4c8c5702dab4af044...  2113635257684733   
26     0x30e5e466cb409bb79f8ad073a51dd25cf14f9b2a6ac2...  2113635794555645   
27     0x6719c21937385c8a8dc59981a46bf684ae04aa864761...  2114668380154367   
28     0xf5e0fae47f4d2f856f8eea85cc61ae5b2f8ae469c8d7...                -1   
29     0xbbb7c235c7dc494c72c6807491d81d2f010ac1890459...                -1   
...                                                  ...               ...   
13865  0x1ad3073c462da39a5bcd15d766511537cc4fb9dd7ff1...                -1   
13866  0x1c0b85a211ef91aace8a0f897540db5328dfce0d99fa...                -1   
13867  0x81d4e7ea9cc4fcbb2b5ac488f25c851cd87f756a72a0...                -1   
13868  0x6ab82117f72e547434bf6bcddc074e0027dc09592e50...  2177361219219123   
13869  0x885e702ffd7dbdaec5b1d7b4bd6cc2bc7e1247f44e0f...                -1   
13870  0xf9d0f0c4def664f15404c421ce1ab89b09da4c209fac...  2178426758358365   
13871  0x791a146ea50e4477703fbcb04cf34243e8f96d9818a5...  2178427295229277   
13872  0x56af39fc916549fc4cfad50df3ba1db8277febb08b95...  2179491517302937   
13873  0xf88f1fb3bddadf91f4902597c335a61a6410b3875a88...  2180556259016282   
13874  0x241bc08a29794a3f7cec6cecfa383ec4ea73906b1d08...                -1   
13875  0x9e6925003f9ba6a869ec2315c1cd98630b62751b36d4...                -1   
13876  0xb2fc0bbfedbe1c1432f58913438b12428d9267e148cd...                -1   
13877  0x50640467a3993dc540dbb34133945c2257e440c00836...  2191595732569029   
13878  0x4405e8a715a5f1861e854851975b5e5f303925ae5c64...                -1   
13879  0x19798f8f54e04f117633257c5189c748870dfa3269b6...  2178414483825576   
13880  0xbf737d15e9a40f25077d41a0500b6038a721e065c78e...                -1   
13881  0x863521b2b552240c6bf0d8d3d7eab7bd50a7562afe21...  2182674026174042   
13882  0xf35f312aafdcb4c627ee6aaae53de3dd72aaed6140ec...                -1   
13883  0x5399cf1fe099c1a53b925cb69805284353577c1f4ba1...  2192667995418614   
13884  0x0f95954c5895fbcbc5d2efa98b87258aae8945cba687...                -1

In [130]:
non_canonical_df = None

In [ ]:
for nc_hash in non_canonical_list:
    non_canonical_df = pd.concat([non_canonical_df, broadcast_df 

In [44]:
with open(AWS_PATH+'2019-07-09.txt', encoding='"ISO-8859-1"') as f:
    while True:
        line = f.readline()
        # print(line)
        if not line:
            break
        if 'Block Hash=' in line:
            b_hash, b_info_list = parse_one_broadcast

[2019-07-09 00:00:00.280321248 +0800 CST m=+10829.192303042] [HandlerNewBlockMsg]Block Hash=0x869d968cbd5404f81d8fa750eb4672f4752db1979474b5ee611fb7ca0eb309d5, parentHash=0xc80ea5c43288306395ec6b09889558aaaf2cdca2fc56f3a5564073c7d94e2ca9, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0xc49fd167b6b3aa92185a33863699777d092a2810ed372407ccc2345d3c3cb56e, nonce=705341863386909553, logsBloom=0221218a04322008408904084268000981003008400000049080104010910140101ac808400041881188400093400188920803400c24900105c228780080049b880880800d4a020011c690880014c30206085800004140040402001406400208204288004a200240111084080000081108841000340a6400000121b80000184004100000010521008c440414d000821020204460508002224b890181101148400000210300801c0103c400a00000884002200480000c000041000100dc02040042144c22406409000a800010042a0c06080021038048080630200182810024512440208800000042010800001c90388340128000003400160630100808002824, number=8111535, miner=0x5A0b54D5dc17e0AadC383d2db43B0

[2019-07-09 00:37:38.191786709 +0800 CST m=+13087.103768540] [HandlerNewBlockMsg]Block Hash=0x1c2a8a9390f614b2e2aa274c39b15a7b0667dd56cea608cb2701977f2e7d8df7, parentHash=0x8a500ad1ef0012fd8784ddc453f7561a688587dd46c190ef79a057288c742d8c, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x26b447742ec077cc01a66377a92fa06515ee27ab782a574d4210474b02b02d14, nonce=4961872397439018755, logsBloom=0204328240e2e0fed29e14461800169442001cb600b4541aa51cc041e40ac0904552181141902a163816480281443129c210345448e490c95360308198280890803440801ac084e3c8a280efc9866428b8940005ae89e42832169771829c2818784124836a86d0304718401340e818401f601a24aa088011082308d012c0200001521ac38667c2020084802c83810014c905b1b3052000c10443c11230ba00292a00180f0188a04803d02a8235d09500c03500008b480724420ae018f8480e0434101dc6086092228505118007201d4424401817451acb1408717008001420f140b1e89d202181c7900801d84c81628492402237d044016d00105484a1e455b4, number=8111705, miner=0x5A0b54D5dc17e0AadC383d2db43B

[2019-07-09 01:20:16.394412747 +0800 CST m=+15645.306394543] [HandlerNewBlockMsg]Block Hash=0x973ecce643436c5e60f149a8ddb6e2fc8eb74d182b6c95789f8c12fa148e70b3, parentHash=0x448392d8150c9aa8ad0a1dd91c88006b4a03c77f5c9dbb5bf795e23db6f8cd1e, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x6eaf6189a12c670e357b925d2a95458717e2b82e97b4c75beddad0e07eb83ad1, nonce=6356401102555559852, logsBloom=920211809040421c683da60321a611412900920113010441e900ac02020b0d182e819484028220144b000d0612401180830230100f058801204bb200c071b0a0c04801461384c011489809e846c8401444109029884a82480072a000444208114060000272010111161860813d530a119c06302030076d288a309950184212188c0030040a0480898090040680048404b0801d305540908082d28002703227200a2010004064a83002000e9840009080324104400b148004208b212c1a9037041021ce421014a0018010400006327004108194049d0b106400404002c436a02150dbfd8844441002140906824498ba865009018106408c0160901506aa394180, number=8111904, miner=0x52bc44d5378309EE2abF1539BF71

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[2019-07-09 10:42:07.178955374 +0800 CST m=+49356.090937167] [Inserted]Block Hash=0x1e67ace8e03c40cfeac1c50eef7bece778b4c0fe7e91c775090ae3505710c86c, parentHash=0xedae0b38517a6f7a4c079934a2d2ce6c30446e8db418a80bd1a337ac04ee482a, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x6cff48af5e8f54652155748eca15d9a0bb045d056a9ae5da963a79838d4b7ed8, nonce=2925674364216868261, logsBloom=a181111060c341042382c402ac8012f90180046bb910800d04858084000e870a048b00e4788491b05c42012326d08b2a8a4c14c14c0ac3ed7692e010d4fa01b080041182ee45855aca0e9209cc9cc00406082180cb08aa481b6153047065d02290f821024f04440081855820088d1ec8daa3122a0a882ae90c34693c040e03a814a2003c22d1106ae0211102820e2038938049575dc40441ad4810820910c07812425c071260b82a009b58a0d41748498100146109408508330153a41b7825c404370d83801420bc1a9302d210001e044c544747243ea40c2544068f4092287ea41929148c383404080340c53824a62511821f08280214b52440de0d287200a2, number=8114432, miner=0x09ab1303d3CcAF5f018CD511146b07A240c702

[2019-07-09 11:09:40.051768646 +0800 CST m=+51008.963750442] [HandlerNewBlockMsg]Block Hash=0x209b6d433ee17744a64debe0d2f59aa678ed0be3c5236c9f478ee0f6818c2767, parentHash=0x28eacac4df52334e507a7531aa2e9b58f1106b571a8b72c207f09ac6f3650658, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x030e390cf79cb59ae67b6dd4391f0184c9a82ae0cc07f71190aa455e9efbc49d, nonce=604382528863751368, logsBloom=0008101044481085a0d00284255c143568c050931d880004ccc0c064a2c0e1020c40004e18da0088e02a6036204013422055020409862902400081821bb4800158817022e230c702ca8114080204242a4a351a0c37a6024d049434754859008981090a834ec0e92d2209500104085a041602e5870870281206a8c2920080620400390d186251480000c000008161451d61c681760b401001c294047a021040a90b006d919105a0009007c28004610e002c01090c20c0c0200216c878903407350290cc438902204014147046030a345520ec042282e5040da29b216811c4f067005080090066900008a8060860042ed450a5400000180000040c159023bc0804, number=8114553, miner=0xEEa5B82B61424dF8020f5feDD8176

[2019-07-09 11:42:36.594387418 +0800 CST m=+52985.506369212] [HandlerNewBlockMsg]Block Hash=0xb8ce75fe45dc991b156074edd7951b6733cb28748fd6685b453889a755335424, parentHash=0x39a719718cbdebded248fd78edb0b769a058b7e67e9c88f506485ced3ee95c81, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x9e315942972d333b5e9270ec0a800f09e3b70f8cd4fe9899c53931c55bd3cd95, nonce=13642232406877530533, logsBloom=84a60009424e1952016100086a0a1c008001308de55000988602a4aa006471081d6a4132c2018004290864403252530406098420040d00058200c3843af00014a02409c0ad060101d044da2e8341540096042101001900c8b048804719422058e00f0b2b6b4421810111c05919ca0805d0c090040461a005012040324410040002980098895b0404000005dc810094d5e7404040d01484833ba20280081a00192304a80120a0288bc6850a9400208011798c05000003888a26015000d020000208181a03630081012444250d026004540c8042050009090c9800208718462801e25014843042100304a006928e8ba810c8e0d030200610045418d419880020c1, number=8114699, miner=0x829BD824B016326A401d083B33D

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[2019-07-09 23:29:27.510492462 +0800 CST m=+95396.422474277] [HandlerNewBlockMsg]Block Hash=0xc36a01fb146a2991d8e9f8068ef019a571c5bd7eef76b05215f1a75c92ec9802, parentHash=0xe784e80dffca5c2bb6a2f4d3eb520cf2a8344d7231d0e025ff441b4ad89053d3, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x415475e6c754490e5f51665c7bf6da431462d09d4be8f0275d6fde6a83ac5305, nonce=14932116727675495173, logsBloom=00200080000028020004000000800200010000000000000000000040000a0000000404002000000000100000020001000008204800028000000040040010002410012800800820200882800880406042040020000a000020000000010120000480000000400480000c08400004500000000000000000014002000110008040004100080000000000000000000000400000402000530000d0c0000000001010b08000008000802000100000a0000a14000100000002000240000a00610000060000300002000000000400000000800400000200000108800400888008401200010000000400000000000000000400200808000001000000000000100000400000, number=8117885, miner=0x002e08000acbbaE2155Fab7AC01

In [21]:
temp_line = '[2019-07-09 00:21:47.952844055 +0800 CST m=+12136.864825886] [HandlerNewBlockMsg]Block Hash=0x71edb48205a4b57f628a9c8f2d50020b48616409b874013bf935481186579720, parentHash=0x6affbffc5670a68a0f0a0f526c8cfb51953883377abb4e059d635420fa4e572f, uncleHash=0x1dcc4de8dec75d7aab85b567b6ccd41ad312451b948a7413f0a142fd40d49347, receiptHash=0x62342b0a5e1d1175c51fd7412baf2385776a93c278b384be6f924c5dc5e8d22e, nonce=18216788707184816079, logsBloom=020a101544444209000c170042a21018095410010410248e01a0c004480a13487896e0008a2800820a8adb28328491970a4b641549a0c581a880e800c128e623041001c00852a537dd02458e00224e00aa0007c40825341197138260918cb1029a2a0004472c5f0280ce40d0200a280c104211f0b204245401200f3c606829640b1308032344201080d14805a04c04182140c8ac33c1946192d00c00705619948b144140414a6028301044ab5000880000204d6900019860591045459890888210180853e902208c6291044a14190206a0c20b07102801042298027489502188e01ce40110b7100d020293c4d282bcc60382221574208015220070402609128c, number=8111636, miner=0xEA674fdDe714fd979de3EdF0F56AA9716B898ec8, uncleNum=0, txNum=187, gasUsed=7976058, gasLimit=8000000, difficulty=2125037248161934, root=0x2bf2d8304d45f47f0d338f41ca110d7cc6aa2870bf3b97fb97aca527df06a06c, mixDigest=0x82928059d8112e0317225104bd8bd824ede87af69a63c0f130142717e7b69f23, size=29.95 KiB, timestamp=2019-07-09 00:21:36 +0800 CST'

b_hash = temp_line.split('Block Hash=')[1].split(', parentHash')[0]
difficulty = temp_line.split('difficulty=')[1].split(', ')[0]
gasLimit = temp_line.split('gasLimit=')[1].split(', ')[0]
gasUsed = temp_line.split('gasUsed=')[1].split(', gasLimit')[0]
logsBloom = temp_line.split('logsBloom=')[1].split(', number=')[0]
miner = temp_line.split('miner=')[1].split(', uncleNum=')[0]
timestamp = temp_line.split('timestamp=')[1]
uncles = temp_line.split('uncleNum=')[1].split(', txNum=')[0]

print('hash: ', b_hash)
print('difficulty: ', difficulty)
print('gasLimit: ', gasLimit)
print('gasUsed: ', gasUsed)
print('logsBloom: ', logsBloom)
print('miner: ', miner)
print('timestamp: ', timestamp)
print('uncles: ', uncles)

hash:  0x71edb48205a4b57f628a9c8f2d50020b48616409b874013bf935481186579720
difficulty:  2125037248161934
gasLimit:  8000000
gasUsed:  7976058
logsBloom:  020a101544444209000c170042a21018095410010410248e01a0c004480a13487896e0008a2800820a8adb28328491970a4b641549a0c581a880e800c128e623041001c00852a537dd02458e00224e00aa0007c40825341197138260918cb1029a2a0004472c5f0280ce40d0200a280c104211f0b204245401200f3c606829640b1308032344201080d14805a04c04182140c8ac33c1946192d00c00705619948b144140414a6028301044ab5000880000204d6900019860591045459890888210180853e902208c6291044a14190206a0c20b07102801042298027489502188e01ce40110b7100d020293c4d282bcc60382221574208015220070402609128c
miner:  0xEA674fdDe714fd979de3EdF0F56AA9716B898ec8
timestamp:  2019-07-09 00:21:36 +0800 CST
uncles:  0


## Canonical Blocks

# Models

## Random Forest